In [1]:
import pandas as pd
import random
import json
import re
import os
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.ensemble import BaggingClassifier
from sklearn.multiclass import OneVsRestClassifier
import joblib
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.svm import SVC
from tqdm import tqdm
import string
import scipy
import nltk
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.tokenize import word_tokenize
stop_words = stopwords.words('english')
stemmer = PorterStemmer()
lemmatizer = WordNetLemmatizer()
import torch
from transformers import BertTokenizer, BertForSequenceClassification
from torch.utils.data import DataLoader
from datasets import load_dataset
import pandas as pd
from sklearn.metrics import f1_score
from IPython.display import HTML, display
from tqdm import tqdm
import spacy
import re
import nltk
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.tokenize import word_tokenize
from nltk.tokenize.treebank import TreebankWordTokenizer
stop_words = stopwords.words('english')
stemmer = PorterStemmer()
lemmatizer = WordNetLemmatizer()
tokenizer = TreebankWordTokenizer()

[nltk_data] Downloading package stopwords to /home/jimbo/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/jimbo/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /home/jimbo/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to /home/jimbo/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/jimbo/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /home/jimbo/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [2]:
data_0 = pd.read_csv('../datasets/fossology-master-corrected.csv')
X_0 = data_0["copyright"]
y_0 = data_0["falsePositive"]
X_0 = X_0.drop_duplicates()
y_0 = y_0[X_0.index]

data_1 = pd.read_csv('../datasets/kubernetes-master-corrected.csv')
X_1 = data_1["copyright"]
y_1 = data_1["falsePositive"]
X_1 = X_1.drop_duplicates()
y_1 = y_1[X_1.index]

data_2 = pd.read_csv('../datasets/tensorflow-master-corrected.csv')
X_2 = data_2["copyright"]
y_2 = data_2["falsePositive"]
X_2 = X_2.drop_duplicates()
y_2 = y_2[X_2.index]

data_3 = pd.read_csv('../datasets/fossology-provided-1-corrected.csv')

X_3 = data_3['copyright']
y_3 = data_3['falsePositive']
X_3 = X_3.drop_duplicates()
y_3 = y_3[X_3.index]

data_4 = pd.read_csv('../datasets/fossology-provided-2.csv')

X_4 = data_4['copyright']
y_4 = data_4['falsePositive']
X_4 = X_4.drop_duplicates()
y_4 = y_4[X_4.index]

data_5 = pd.read_csv('../datasets/feature-extraction-paper.csv')

X_5 = data_5['copyright']
y_5 = data_5['falsePositive']
X_5 = X_5.drop_duplicates()
y_5 = y_5[X_5.index]

X = pd.concat([X_0, X_1, X_2, X_3])
y = pd.concat([y_0, y_1, y_2, y_3])

X = X.reset_index(drop=True)
y = y.reset_index(drop=True)

print('Class 0 Percentage: ', len(y[y == 0]) / len(y))
print('Class 1 Percentage: ', len(y[y == 1]) / len(y))

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, shuffle=True)

Class 0 Percentage:  0.7522737712448323
Class 1 Percentage:  0.24772622875516767


In [3]:
def aggregate_reports(reports, print_aggregates=True):
    import pandas as pd
    import numpy as np
    dfs = []
    for metric in ['precision', 'recall', 'f1-score']:
        scores = []
        for report in reports:
            scores.append([report['0'][metric], report['1'][metric]])
        scores = np.array(scores)
        scores = scores[:, :2]
        mean_scores = np.mean(scores, axis=0)
        mean_scores = [f"{score:.6f}" for score in mean_scores]
        df = pd.DataFrame(scores, columns=['0', '1'])
        df.loc['Mean'] = mean_scores
        df['Metric'] = metric
        dfs.append(df)
    if print_aggregates:
        print("## Precision")
        print(dfs[0].to_markdown())
        print("## Recall")
        print(dfs[1].to_markdown())
        print("## F1-score")
        print(dfs[2].to_markdown())
    else:
        return dfs[0], dfs[1], dfs[2]

def get_missclassified_rows(X, y_true, y_pred, only_this_class = [0, 1], return_index=False):
    if type(y_true) != list:
        y_true = y_true.tolist()
    if type(y_pred) != list:
        y_pred = y_pred.tolist()
    if type(X) != list:
        X = X.tolist()
    missclassified_rows = []
    for i in range(len(y_true)):
        if y_true[i] != y_pred[i] and y_true[i] in only_this_class:
            missclassified_rows.append(i)
    if return_index:
        return [(y_pred[i], i, X[i]) for i in missclassified_rows]
    else:
        return [(y_pred[i], X[i]) for i in missclassified_rows]

def preprocess_function(sentences, lower=False, replace_copyright_symbols=False,
                        replace_dates=False, remove_numbers=False, remove_punctuation=False,
                        remove_special_characters=False, remove_whitespaces=False, remove_specials_weird=False,
                        remove_stopwords=False, replace_emails=False,
                        tokenize=False, lemmatize=False, glove=False, remove_endlines=False,
                        replace_copyright_symbol_v2=False, replace_entities=False, spacy_model=None):
    if type(sentences) is not list:
        sentences = sentences.to_list()
    for i in range(len(sentences)):
        sentences[i] = str(sentences[i])
    if replace_entities:
        if spacy_model is None: # give error
            raise ValueError('spacy_model must be provided if replace_entities is True')
        else:
            nlp = spacy_model
        sentences = [nlp(sentence) for sentence in sentences]
        new_sentences = []
        for sentence in sentences:
            new_sentence = sentence.text
            for entity in sentence.ents:
                if entity.label_ == 'ENT':
                    new_sentence = re.sub(re.escape(entity.text), ' ENTITY ', new_sentence)
            new_sentences.append(new_sentence)
        sentences = new_sentences
    if replace_dates:
        if glove:
            sentences = [re.sub(r'\d{4}', ' <DATE> ', sentence) for sentence in sentences]
        else:
            sentences = [re.sub(r'\d{4}', ' DATE ', sentence) for sentence in sentences]
    if remove_numbers:
        sentences = [re.sub(r'\d+', ' ', sentence) for sentence in sentences]
    if replace_copyright_symbols:
        if glove:
            symbol_text = ' <COPYRIGHT SYMBOL> '
        else:
            symbol_text = ' COPYRIGHTSYMBOL '
        sentences = [re.sub(r'©', symbol_text, sentence) for sentence in sentences]
        sentences = [re.sub(r'\(c\)', symbol_text, sentence) for sentence in sentences]
        sentences = [re.sub(r'\(C\)', symbol_text, sentence) for sentence in sentences]
    if replace_copyright_symbol_v2:
        if glove:
            symbol_text = ' <COPYRIGHT SYMBOL> '
        else:
            symbol_text = ' COPYRIGHT SYMBOL '
        sentences = [re.sub(r'©', symbol_text, sentence) for sentence in sentences]
        sentences = [re.sub(r'\(c\)', symbol_text, sentence) for sentence in sentences]
        sentences = [re.sub(r'\(C\)', symbol_text, sentence) for sentence in sentences]
    if replace_emails:
        if glove:
            email_text = ' <EMAIL> '
        else:
            email_text = ' EMAIL '
        sentences = [re.sub("""(?:[a-z0-9!#$%&'*+/=?^_`{|}~-]+(?:\.[a-z0-9!#$%&'*+/=?^_`{|}~-]+)*|"(?:[\x01-\x08\x0b\x0c\x0e-\x1f\x21\x23-\x5b\x5d-\x7f]|\\[\x01-\x09\x0b\x0c\x0e-\x7f])*")@(?:(?:[a-z0-9](?:[a-z0-9-]*[a-z0-9])?\.)+[a-z0-9](?:[a-z0-9-]*[a-z0-9])?|\[(?:(?:(2(5[0-5]|[0-4][0-9])|1[0-9][0-9]|[1-9]?[0-9]))\.){3}(?:(2(5[0-5]|[0-4][0-9])|1[0-9][0-9]|[1-9]?[0-9])|[a-z0-9-]*[a-z0-9]:(?:[\x01-\x08\x0b\x0c\x0e-\x1f\x21-\x5a\x53-\x7f]|\\[\x01-\x09\x0b\x0c\x0e-\x7f])+)\])""", email_text, sentence) for sentence in sentences]
    if tokenize:
        if not glove:
            sentences = [''.join(tokenizer.tokenize(sentence)) for sentence in sentences]
        else:
            sentences = [tokenizer.tokenize(sentence) for sentence in sentences]
    if lemmatize:
        lemmatizer = WordNetLemmatizer()
        if not glove:
            sentences = [''.join([lemmatizer.lemmatize(word) for word in sentence]) for sentence in sentences]
        else:
            sentences = [[lemmatizer.lemmatize(word) for word in sentence] for sentence in sentences]
    if remove_punctuation:
        sentences = [re.sub(r'[^\w\s]', ' ', sentence) for sentence in sentences]
    if remove_special_characters:
        sentences = [re.sub(r'[^a-zA-Z0-9]', ' ', sentence) for sentence in sentences]
    if remove_specials_weird:
        sentences = [re.sub(r'[^a-zA-Z0-9]', '', sentence) for sentence in sentences]
    if lower:
        sentences = [sentence.lower() for sentence in sentences]
    if remove_stopwords:
        sentences = [re.sub(r'\b(?:{})\b'.format('|'.join(stopwords.words('english'))), ' ', sentence)
                     for sentence in sentences]
    if remove_endlines:
        sentences = [re.sub(r'\n', ' ', sentence) for sentence in sentences]
    if remove_whitespaces:
        sentences = [re.sub(r' {2,}', ' ', sentence) for sentence in sentences]
    return sentences

def train(svm, vectorizer, threshold, preprocess_function,**kwargs):
    X_train_tfidf = vectorizer.fit_transform(preprocess_function(X_train, **kwargs))
    X_test_tfidf = vectorizer.transform(preprocess_function(X_test, **kwargs))
    X_1_tfidf = vectorizer.transform(preprocess_function(X_1, **kwargs))
    X_2_tfidf = vectorizer.transform(preprocess_function(X_2, **kwargs))
    X_3_tfidf = vectorizer.transform(preprocess_function(X_3, **kwargs))
    preprocessed_X = preprocess_function(X, **kwargs)
    X_tfidf = vectorizer.transform(preprocessed_X)
    svm.fit(X_train_tfidf, y_train)
    if True: #svm.probability:
        y_pred = svm.predict_proba(X_test_tfidf)
        y_pred_1 = svm.predict_proba(X_1_tfidf)
        y_pred_2 = svm.predict_proba(X_2_tfidf)
        y_pred_3 = svm.predict_proba(X_3_tfidf)
        y_pred_4 = svm.predict_proba(X_tfidf)
        if threshold is None:
            y_pred_classification = np.argmax(y_pred, axis=1)
            y_pred_1_classification = np.argmax(y_pred_1, axis=1)
            y_pred_2_classification = np.argmax(y_pred_2, axis=1)
            y_pred_3_classification = np.argmax(y_pred_3, axis=1)
            y_pred_4_classification = np.argmax(y_pred_4, axis=1)
        else:
            y_pred_classification = [np.argmax(y) if max(y) > threshold else 0 for y in y_pred]
            y_pred_1_classification = [np.argmax(y) if max(y) > threshold else 0 for y in y_pred_1]
            y_pred_2_classification = [np.argmax(y) if max(y) > threshold else 0 for y in y_pred_2]
            y_pred_3_classification = [np.argmax(y) if max(y) > threshold else 0 for y in y_pred_3]
            y_pred_4_classification = [np.argmax(y) if max(y) > threshold else 0 for y in y_pred_4]
    else:
        y_pred_classification = svm.predict(X_test_tfidf)
        y_pred_1_classification = svm.predict(X_1_tfidf)
        y_pred_2_classification = svm.predict(X_2_tfidf)
        y_pred_3_classification = svm.predict(X_3_tfidf)
        y_pred_4_classification = svm.predict(X_tfidf)
    report = classification_report(y_test, y_pred_classification, output_dict=True)
    report_1 = classification_report(y_1, y_pred_1_classification, output_dict=True)
    report_2 = classification_report(y_2, y_pred_2_classification, output_dict=True)
    report_3 = classification_report(y_3, y_pred_3_classification, output_dict=True)
    report_4 = classification_report(y, y_pred_4_classification, output_dict=True)
    miss_classified_rows_0 = get_missclassified_rows(preprocessed_X, y, y_pred_4_classification, only_this_class=[0], return_index=True)
    miss_classified_rows_1 = get_missclassified_rows(preprocessed_X, y, y_pred_4_classification, only_this_class=[1], return_index=True)
    #aggregate_reports([report, report_1, report_2, report_3, report_4])
    print('Number of missclassifications in class 0: ', report_4['0']['support'] - round(report_4['0']['recall'] * report_4['0']['support']), 'out of a total sample of: ', report_4['0']['support'], ' - about ', round((1 - report_4['0']['recall']) * 100, 2), '% of the class was missclassified')
    print('Number of missclassifications in class 1: ', report_4['1']['support'] - round(report_4['1']['recall'] * report_4['1']['support']), 'out of a total sample of: ', report_4['1']['support'], ' - about ', round((1 - report_4['1']['recall']) * 100, 2), '% of the class was missclassified')
    return svm, vectorizer, miss_classified_rows_0, miss_classified_rows_1, preprocessed_X

In [4]:
# Write only the copyrights to disk to import to doccano
# Use the current NER model to label the entire dataset and go through it using doccano once more
# to label the entities that were not labeled correctly

def text_to_doccano(sentences):
    """
    :text (str): source text
    Returns (list (dict)): deccano format json
    """
    djson = list()
    #doc = nlp(text)
    for sentence in tqdm(sentences):
        labels = list()
        djson.append({'text': sentence, "labels": labels})
    return djson

doccano_json = text_to_doccano(X[y == 0])
with open('copyrights-ner.jsonl', 'w') as f:
    for item in doccano_json:
        f.write(json.dumps(item) + '\n')

100%|██████████| 16377/16377 [00:00<00:00, 1355101.93it/s]

In [5]:
# Convert JSONL to spacy compatible format
import json
import spacy
from spacy.tokens import Doc, DocBin
from spacy.training import Example
from spacy.util import minibatch

def load_data(file_path):
    """
    Load JSONL data from a file and convert it to spaCy's training format.
    :param file_path: The path of the JSONL file.
    :return: A list of training examples.
    """
    data = []
    with open(file_path, 'r') as f:
        for line in f:
            item = json.loads(line)
            text = item['text']
            entities = [(e[0], e[1], e[2]) for e in item['label']]
            data.append((text, {'entities': entities}))
    return data

def save_data(data, file_path):
    """
    Save data in spaCy's binary format.
    :param data: The training data.
    :param file_path: The path of the output file.
    """
    nlp = spacy.blank('en')
    doc_bin = DocBin()
    for text, annotations in data:
        doc = nlp.make_doc(text)
        example = Example.from_dict(doc, annotations)
        doc_bin.add(example.reference)
    doc_bin.to_disk(file_path)

In [ ]:
data = load_data('../NER_datasets/default/declutter-data/600.jsonl')
save_data(data, '../NER_datasets/spacy_compatible/declutter-data/600.spacy')

In [4]:
# split the 600 documents into train and test - 80, 20 split.
doc_bin = spacy.tokens.DocBin().from_disk('../NER_datasets/spacy_compatible/declutter-data/600.spacy')
nlp = spacy.load("en_core_web_sm")
docs = list(doc_bin.get_docs(nlp.vocab))
train_docs, test_docs = train_test_split(docs, test_size=0.2, random_state=42, shuffle=True)
train_doc_bin = spacy.tokens.DocBin(docs=train_docs)
test_doc_bin = spacy.tokens.DocBin(docs=test_docs)
train_doc_bin.to_disk('../NER_datasets/spacy_compatible/declutter-data/600-train.spacy')
test_doc_bin.to_disk('../NER_datasets/spacy_compatible/declutter-data/600-valid.spacy')

/home/jimbo/pythondeps/spacy/util.py:910: UserWarning: [W095] Model 'en_core_web_sm' (3.5.0) was trained with spaCy v3.5.0 and may not be 100% compatible with the current version (3.6.1). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [5]:
!python -m spacy debug data '../NER_configs/train-declutter-600.cfg'


============================ Data file validation ============================
✔ Pipeline can be initialized with data
✔ Corpus is loadable

=============================== Training stats ===============================
Language: en
Training pipeline: tok2vec, ner
480 training docs
120 evaluation docs
✔ No overlap between training and evaluation data
⚠ Low number of examples to train a new pipeline (480)

============================== Vocab & Vectors ==============================
ℹ 5592 total word(s) in the data (884 unique)
ℹ No word vectors present in the package

========================== Named Entity Recognition ==========================
ℹ 1 label(s)
0 missing value(s) (tokens with '-' label)
✔ Good amount of examples for all labels
✔ Examples without occurrences available for all labels
✔ No entities consisting of or starting/ending with whitespace
✔ No entities crossing sentence boundaries

================================== Summary ==================================
✔ 7 che

In [6]:
!python -m spacy train '../NER_configs/train-declutter-600.cfg' --output '../NER_models/declutter-600'

✔ Created output directory: ../NER_models/declutter-600
ℹ Saving to output directory: ../NER_models/declutter-600
ℹ Using CPU

=========================== Initializing pipeline ===========================
✔ Initialized pipeline

============================= Training pipeline =============================
ℹ Pipeline: ['tok2vec', 'ner']
ℹ Initial learn rate: 0.001
E    #       LOSS TOK2VEC  LOSS NER  ENTS_F  ENTS_P  ENTS_R  SCORE 
---  ------  ------------  --------  ------  ------  ------  ------
  0       0          0.00     62.67   27.19   20.93   38.79    0.27
  3     200         69.82   1115.53   92.17   92.98   91.38    0.92
  8     400         69.18     85.76   93.10   93.10   93.10    0.93
 13     600         56.97     73.04   93.51   93.91   93.10    0.94
 20     800         71.35     60.70   91.30   92.11   90.52    0.91
 29    1000         88.62     58.24   91.77   92.17   91.38    0.92
 39    1200        330.92     72.70   93.04   93.86   92.24    0.93
 52    1400        845

In [7]:
# Compare fine tuning the standard en_core_web_sm model
# with the model trained on the declutter dataset

nlp = spacy.load('en_core_web_sm')
nlp.to_disk('../NER_models/en_core_web_sm')

/home/jimbo/pythondeps/spacy/util.py:910: UserWarning: [W095] Model 'en_core_web_sm' (3.5.0) was trained with spaCy v3.5.0 and may not be 100% compatible with the current version (3.6.1). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [9]:
nlp = spacy.load("../NER_models/declutter-600/model-best")
X_decluttered_600_copyrights = [nlp(sentence) for sentence in tqdm(X[y == 0])]

100%|██████████| 16377/16377 [00:38<00:00, 427.65it/s]


In [12]:
spacy.displacy.serve(X_decluttered_600_copyrights[0:1000], style="ent", auto_select_port=True)


Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [13]:
spacy.displacy.serve(X_decluttered_600_copyrights[13000:14000], style="ent", auto_select_port=True)


Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [6]:
nlp = spacy.load("../NER_models/declutter-600/model-best")
X_5_decluttered_600 = [nlp(sentence) for sentence in tqdm(X_5[y_5 == 0])]

100%|██████████| 1977/1977 [00:04<00:00, 463.34it/s]


In [7]:
spacy.displacy.serve(X_5_decluttered_600, style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)
/home/jimbo/pythondeps/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [10]:
nlp = spacy.load("../NER_models/declutter-600/model-best")
X_decluttered_600_false_positives = [nlp(sentence) for sentence in tqdm(X[y == 1])]

100%|██████████| 5393/5393 [00:14<00:00, 378.43it/s]


In [11]:
spacy.displacy.serve(X_decluttered_600_false_positives[0:1000], style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)
/home/jimbo/pythondeps/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


##  Declutter after updating the dataset

In [6]:
# Examples of interest
data = load_data('../NER_datasets/default/declutter-data/750.jsonl')
save_data(data, '../NER_datasets/spacy_compatible/declutter-data/750.spacy')

/home/jimbo/pythondeps/spacy/training/iob_utils.py:149: UserWarning: [W030] Some entities could not be aligned in the text "Copyright (C) 1991, 1999 Free Software Foundation,..." with entities "[(0, 54, 'Copyright')]". Use `spacy.training.offsets_to_biluo_tags(nlp.make_doc(text), entities)` to check the alignment. Misaligned entities ('-') will be ignored during training.
  warnings.warn(
/home/jimbo/pythondeps/spacy/training/iob_utils.py:149: UserWarning: [W030] Some entities could not be aligned in the text "Copyright (C) 1991 Free Software Foundation, Inc. ..." with entities "[(0, 48, 'Copyright')]". Use `spacy.training.offsets_to_biluo_tags(nlp.make_doc(text), entities)` to check the alignment. Misaligned entities ('-') will be ignored during training.
  warnings.warn(
/home/jimbo/pythondeps/spacy/training/iob_utils.py:149: UserWarning: [W030] Some entities could not be aligned in the text "Copyright (c) 1999-2002 Zend Technologies Ltd. All..." with entities "[(0, 45, 'Copyright')]

In [7]:
# split the 750 documents into train and test - 80, 20 split.
doc_bin = spacy.tokens.DocBin().from_disk('../NER_datasets/spacy_compatible/declutter-data/750.spacy')
nlp = spacy.load("en_core_web_sm")
docs = list(doc_bin.get_docs(nlp.vocab))
train_docs, test_docs = train_test_split(docs, test_size=0.2, random_state=42, shuffle=True)
train_doc_bin = spacy.tokens.DocBin(docs=train_docs)
test_doc_bin = spacy.tokens.DocBin(docs=test_docs)
train_doc_bin.to_disk('../NER_datasets/spacy_compatible/declutter-data/750-train.spacy')
test_doc_bin.to_disk('../NER_datasets/spacy_compatible/declutter-data/750-valid.spacy')

/home/jimbo/pythondeps/spacy/util.py:910: UserWarning: [W095] Model 'en_core_web_sm' (3.5.0) was trained with spaCy v3.5.0 and may not be 100% compatible with the current version (3.6.1). If you see errors or degraded performance, download a newer compatible model or retrain your custom model with the current spaCy version. For more details and available updates, run: python -m spacy validate
  warnings.warn(warn_msg)


In [8]:
!python -m spacy debug data '../NER_configs/train-declutter-750.cfg'


============================ Data file validation ============================
✔ Pipeline can be initialized with data
✔ Corpus is loadable

=============================== Training stats ===============================
Language: en
Training pipeline: tok2vec, ner
600 training docs
150 evaluation docs
✔ No overlap between training and evaluation data
⚠ Low number of examples to train a new pipeline (600)

============================== Vocab & Vectors ==============================
ℹ 7133 total word(s) in the data (1120 unique)
ℹ No word vectors present in the package

========================== Named Entity Recognition ==========================
ℹ 1 label(s)
0 missing value(s) (tokens with '-' label)
✔ Good amount of examples for all labels
✔ Examples without occurrences available for all labels
✔ No entities consisting of or starting/ending with whitespace
✔ No entities crossing sentence boundaries

================================== Summary ==================================
✔ 7 ch

In [9]:
!python -m spacy train '../NER_configs/train-declutter-750.cfg' --output '../NER_models/declutter-750'

✔ Created output directory: ../NER_models/declutter-750
ℹ Saving to output directory: ../NER_models/declutter-750
ℹ Using CPU

=========================== Initializing pipeline ===========================
✔ Initialized pipeline

============================= Training pipeline =============================
ℹ Pipeline: ['tok2vec', 'ner']
ℹ Initial learn rate: 0.001
E    #       LOSS TOK2VEC  LOSS NER  ENTS_F  ENTS_P  ENTS_R  SCORE 
---  ------  ------------  --------  ------  ------  ------  ------
  0       0          0.00     76.83   83.96   83.67   84.25    0.84
  2     200         74.42   1201.60   83.85   84.14   83.56    0.84
  6     400        117.73    176.07   85.62   85.62   85.62    0.86
 10     600        139.56    117.25   86.30   86.30   86.30    0.86
 16     800        136.82    130.29   88.36   88.36   88.36    0.88
 22    1000        146.29    107.13   87.37   87.07   87.67    0.87
 30    1200        101.06     94.23   86.99   86.99   86.99    0.87
 40    1400        117

In [10]:
nlp = spacy.load("../NER_models/declutter-750/model-best")
X_decluttered_750 = [nlp(sentence) for sentence in tqdm(X[y == 0])]
X_decluttered_750_fp = [nlp(sentence) for sentence in tqdm(X[y == 1])]
X_5_decluttered_750 = [nlp(sentence) for sentence in tqdm(X_5[y_5 == 0])]

100%|██████████| 1977/1977 [00:04<00:00, 492.72it/s]


In [11]:
# X copyrights
spacy.displacy.serve(X_decluttered_750[0:1000], style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)
/home/jimbo/pythondeps/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [12]:
spacy.displacy.serve(X_decluttered_750[1001:2000], style="ent", auto_select_port=True)


Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [14]:
spacy.displacy.serve(X_decluttered_750[2001:3000], style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [15]:
spacy.displacy.serve(X_decluttered_750[3001:4000], style="ent", auto_select_port=True)


Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [ ]:
# X copyrights
spacy.displacy.serve(X_decluttered_750[13001:14000], style="ent", auto_select_port=True)

In [ ]:
spacy.displacy.serve(X_5_decluttered_600, style="ent", auto_select_port=True)

In [13]:
def text_to_doccano(sentences):
    """
    :text (str): source text
    Returns (list (dict)): deccano format json
    """
    djson = list()
    #doc = nlp(text)
    for sentence in tqdm(sentences):
        labels = list()
        for e in sentence.ents:
            labels.append([e.start_char, e.end_char, e.label_])
        djson.append({'text': sentence.text, "labels": labels})
    return djson

doccano_json = text_to_doccano(X_decluttered_750)
with open('dataset-decluttered.jsonl', 'w') as f:
    for item in doccano_json:
        f.write(json.dumps(item) + '\n')

100%|██████████| 16377/16377 [00:00<00:00, 104167.48it/s]


In [19]:
data = load_data('../NER_datasets/default/declutter-data/1-3500-corrected-full-dataset.jsonl')
save_data(data, '../NER_datasets/spacy_compatible/declutter-data/1-3500-corrected-full-dataset.spacy')
# split the 750 documents into train and test - 80, 20 split.
doc_bin = spacy.tokens.DocBin().from_disk('../NER_datasets/spacy_compatible/declutter-data/1-3500-corrected-full-dataset.spacy')
nlp = spacy.load("en_core_web_sm")
docs = list(doc_bin.get_docs(nlp.vocab))
train_docs, test_docs = train_test_split(docs, test_size=0.2, random_state=42, shuffle=True)
train_doc_bin = spacy.tokens.DocBin(docs=train_docs)
test_doc_bin = spacy.tokens.DocBin(docs=test_docs)
train_doc_bin.to_disk('../NER_datasets/spacy_compatible/declutter-data/1-3500-corrected-full-dataset-train.spacy')
test_doc_bin.to_disk('../NER_datasets/spacy_compatible/declutter-data/1-3500-corrected-full-dataset-valid.spacy')

In [20]:
!python -m spacy debug data '../NER_configs/train-declutter-1-3500-corrected-full-dataset.cfg'


============================ Data file validation ============================
✔ Pipeline can be initialized with data
✔ Corpus is loadable

=============================== Training stats ===============================
Language: en
Training pipeline: tok2vec, ner
13101 training docs
3276 evaluation docs
⚠ 73 training examples also in evaluation data

============================== Vocab & Vectors ==============================
ℹ 197876 total word(s) in the data (11865 unique)
ℹ No word vectors present in the package

========================== Named Entity Recognition ==========================
ℹ 1 label(s)
0 missing value(s) (tokens with '-' label)
✘ 6 invalid whitespace entity spans
✔ Good amount of examples for all labels
✔ Examples without occurrences available for all labels
✔ No entities crossing sentence boundaries
Entity spans consisting of or starting/ending with whitespace characters are
considered invalid.

================================== Summary =======================

In [21]:
!python -m spacy train '../NER_configs/train-declutter-1-3500-corrected-full-dataset.cfg' --output '../NER_models/declutter-1-3500-corrected-full-dataset'

✔ Created output directory:
../NER_models/declutter-1-3500-corrected-full-dataset
ℹ Saving to output directory:
../NER_models/declutter-1-3500-corrected-full-dataset
ℹ Using CPU

=========================== Initializing pipeline ===========================
✔ Initialized pipeline

============================= Training pipeline =============================
ℹ Pipeline: ['tok2vec', 'ner']
ℹ Initial learn rate: 0.001
E    #       LOSS TOK2VEC  LOSS NER  ENTS_F  ENTS_P  ENTS_R  SCORE 
---  ------  ------------  --------  ------  ------  ------  ------
  0       0          0.00     81.00   73.32   73.72   72.92    0.73
  0     200         71.49   1168.30   86.49   86.89   86.08    0.86
  0     400         97.01    352.01   91.72   92.32   91.12    0.92
  0     600         98.38    339.93   92.54   92.80   92.27    0.93
  0     800        152.64    364.73   93.68   94.09   93.27    0.94
  0    1000        286.06    447.56   94.68   95.10   94.26    0.95
  1    1200        270.22    482.72   

In [22]:
nlp = spacy.load("../NER_models/declutter-1-3500-corrected-full-dataset/model-best")
X_decluttered_750_1 = [nlp(sentence) for sentence in tqdm(X[y == 0])]
X_decluttered_750_fp_1 = [nlp(sentence) for sentence in tqdm(X[y == 1])]
X_5_decluttered_750_1 = [nlp(sentence) for sentence in tqdm(X_5[y_5 == 0])]

100%|██████████| 1977/1977 [00:04<00:00, 459.65it/s]


In [23]:
spacy.displacy.serve(X_decluttered_750[4001:5000], style="ent", auto_select_port=True)


Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [ ]:
spacy.displacy.serve(X_decluttered_750[5001:6000], style="ent", auto_select_port=True)

In [24]:
spacy.displacy.serve(X_decluttered_750[12001:13000], style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [27]:
# X_5 copyrights
spacy.displacy.serve(X_5_decluttered_750_1, style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)
/home/jimbo/pythondeps/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [28]:
# X false positives
spacy.displacy.serve(X_decluttered_750_fp[0:1000], style="ent", auto_select_port=True)


Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [31]:
# Test decluttering
X_decluttered_750_1_cleaned = [' '.join([ent.text for ent in sentence.ents]) for sentence in X_decluttered_750_1]

In [35]:
X_decluttered_750_1[12001:12020]

[Copyright (c) InQuant GmbH Stefan Eletzhofer <stefan.eletzhofer@inquant.de>,
 Copyright (C) 2004 W.J. van der Laan <gnufnork@hetdigitalegat.nl>,
 Copyright (c) 2001 Bill Bumgarner <bbum@friday.com> License: MIT, see below.,
 Copyright: Gael Varoquaux <gael.varoquaux@normalesup.org>,
 Copyright (C) 2005 Jörgen Stenarson <jorgen.stenarson@bostream.nu>,
 Copyright (C) 2001 Python Software Foundation, www.python.org Taken from Python2.2, License: PSF - see below.,
 Copyright (c) 2001, 2002, 2003, 2004 Fernando Perez <fperez@colorado.edu>.,
 Copyright (c) 2001 Janko Hauser <jhauser@zscout.de> and Nathaniel Gray n8gray@caltech.edu>.,
 Copyright (C) 2001 Python Software Foundation, www.python.org</s> Taken from Python2.2, License: PSF - see below.,
 Copyright (c) 2001 Bill Bumgarner <bbum@friday.com></s> License: MIT, see below.,
 copyright, i.e., "<s>Copyright (c) 2001, 2002, 2003, 2004, 2005, 2006 Python Software Foundation; All Rights Reserved</s>" are retained in Python alone or in any d

In [36]:
X_decluttered_750_1_cleaned[12001:12020]

['Copyright (c) InQuant GmbH Stefan Eletzhofer <stefan.eletzhofer@inquant.de>',
 'Copyright (C) 2004 W.J. van der Laan <gnufnork@hetdigitalegat.nl>',
 'Copyright (c) 2001 Bill Bumgarner <bbum@friday.com>',
 'Copyright: Gael Varoquaux <gael.varoquaux@normalesup.org>',
 'Copyright (C) 2005 Jörgen Stenarson <jorgen.stenarson@bostream.nu>',
 'Copyright (C) 2001 Python Software Foundation, www.python.org Taken from Python2.2,',
 'Copyright (c) 2001, 2002, 2003, 2004 Fernando Perez <fperez@colorado.edu>',
 'Copyright (c) 2001 Janko Hauser <jhauser@zscout.de> and Nathaniel Gray n8gray@caltech.edu>.',
 'Copyright (C) 2001 Python Software Foundation Taken from Python2.2,',
 'Copyright (c) 2001 Bill Bumgarner <bbum@friday.com></s>',
 'copyright, i.e., "<s>Copyright (c) 2001, 2002, 2003, 2004, 2005, 2006 Python Software Foundation',
 'Copyright (c) 2001, 2002, 2003, 2004 Fernando Perez <fperez@colorado.edu>.</s>',
 'Copyright (C) 2005 Jörgen Stenarson <jorgen.stenarson@bostream.nu></s>',
 'Copyri

In [37]:
test = 'Copyright (C) 2007 Free Software Foundation, Inc. <https://fsf.org/> Everyone is permitted to copy and distribute verbatim copies of this license document, but changing it is not allowed.'
test_decluttered = nlp(test)

In [39]:
spacy.displacy.serve(test_decluttered, style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.


In [3]:
import spacy
nlp = spacy.load("../NER_models/declutter-1-3500-corrected-full-dataset/model-best")
test = 'Copyright 2012, Seth Vidal <skvidal@fedoraproject.org>'
test_decluttered = nlp(test)
spacy.displacy.serve(test_decluttered, style="ent", auto_select_port=True)

/home/jimbo/pythondeps/spacy/displacy/__init__.py:106: UserWarning: [W011] It looks like you're calling displacy.serve from within a Jupyter notebook or a similar environment. This likely means you're already running a local web server, so there's no need to make displaCy start another one. Instead, you should be able to replace displacy.serve with displacy.render to show the visualization.
  warnings.warn(Warnings.W011)



Using the 'ent' visualizer
Serving on http://0.0.0.0:5000 ...

Shutting down server on port 5000.
